# Answer to Question 1

## Tracking System
I am not familiar with web tracking, but I assume something similar to Google Analytics can be used to track user events. Basically embed a small script to capture user operations (click a page, view video, etc), and send them to the backend data collector to process. It can also capture info such as cookies, geolocation, and ip addresses.

The event structure may look like this (take google analytics event as an example):

```
clientId  (optional)
ipaddress (optional)
geolocation (optional)
timestamp  
eventCategory (e.g. "OutboundLink)
eventAction (e.g. 'click')
eventLabel (e.g. href clicked)
eventValue (optional)
```

## Data Pipeline
With the popularity of Outdoorsy, we would expect tons of tracking events. A scalable solution is required. 

The web tracking events may also merge with events from other data sources to provide better insight. We can image the overall architecture looks like this:  

```
browser event source
(generate tracking events)  ---> streaming platform    ----->   analytics platform      ---->   serving layer 
                                   (kinesis or kafka)            (spark or flink)
                                       ^                        on top of hadoop/s3
                                       | \
                                       |  \                          |
                                      other event sources         <--| (firing events)  

```
Let's take a look at each component.

### Streaming Platform
The streaming platform works as an event bus. Events from different data sources all go through the streaming platform. It is also a buffer to the analytics platform (in case it went down, we still have the data on the streaming cluster). Both Apache Kafka and AWS Kinesis are good candidates for this component. They are both scalable and fast. AWS provides managed services to both of them. The benefit of using Apache Kafka is it's not tied to Amazon. 

### Analytics Platform
We still need to aggregate/corelate events from different sources to generate insight. This is where analytics platform comes into the picture. 

Apache Spark and Apache Flink can both be used in this case. (We can even put an Elasticsearch cluster here.)
Apache Spark should be treated as a successor to Hadoop since it provides an easier-to-user interface for map/reduce and is fast (by loading data into memory). We will see in next question how it is used to generate inverted index.

Apache Flink (or Spark Streaming) can be used to handle realtime event processing (while Spark Jobs are mainly reserved to do batch processing).  

The boundary between streaming platform and analytics platform is not clear cut. For example, AWS Kinesis Analytics also integrates analytics features to do anomaly detection.

Results from the analytics platform can also loop back to the streaming platform for further processing.

### Serving Layer
Other components may be interested in the final pipeline result, hence a serving layer provides query and other services to satisfy this need. Its purpose is highly depending on the use cases.
                               

# Answer to Question 2



## Setup Local Spark
I am using a local spark to run this notebook. Do the following
1. install JDK 8 
2. install python3 and other packages (I use anaconda)
3. download and install Apache Spark (I had 2.2.1 installed on $Home/Software already)
4. install pyspark (pip3 install pyspark to your environment)
5. set the following env before you start the notebook in where you clone the git repo.

```
export SPARK_HOME=${HOME}/Software/spark-2.2.1
export PYSPARK_DRIVER_PYTHON=jupyter
export PYSPARK_DRIVER_PYTHON_OPTS='notebook'
export PYSPARK_SUBMIT_ARGS=--master local[2] pyspark-shell
```

## Start Notebook
Simply run 'pyspark'.

```
% pyspark
```

## Job I Create Dictionary

In [2]:
from pyspark.sql import SparkSession

In [3]:
spark = SparkSession.builder.appName("Test").getOrCreate()

In [4]:
words = spark.sparkContext.textFile("dataset/*").flatMap(lambda line: line.split(" "))

In [5]:
# merge all word appearances into 1
wordCount = words.map(lambda word: (word, 1)).reduceByKey(lambda a,b:a +b)

In [6]:
df = wordCount.zipWithIndex().toDF()

In [7]:
df

DataFrame[_1: struct<_1:string,_2:bigint>, _2: bigint]

In [8]:
df = df.withColumn('word', df['_1'].getItem("_1"))

In [9]:
df = df.withColumnRenamed("_2", "index").drop("_1")

In [10]:
# merge all partitions, csv file will be generated under "dictionary" directory
# make sure "dictionary" does not exist or you get error
df.repartition(1).write.csv("dictionary")

In [11]:
all_words = df.repartition(1).collect()

## Job II Generate Inverted Index

I am a bit lazy here. Instead of reading the dictionary from the just generated csv file, I reuse the one already load in memory.

In [12]:
# we still have this in memory
all_words

[Row(index=0, word='of'),
 Row(index=1, word=''),
 Row(index=2, word='before'),
 Row(index=3, word='Both'),
 Row(index=4, word='official'),
 Row(index=5, word='91'),
 Row(index=6, word='two'),
 Row(index=7, word='rather'),
 Row(index=8, word='away'),
 Row(index=9, word='[10,000'),
 Row(index=10, word='2001,'),
 Row(index=11, word='raising'),
 Row(index=12, word='directly'),
 Row(index=13, word='login:'),
 Row(index=14, word='password:'),
 Row(index=15, word='pub/docs/books/gutenberg'),
 Row(index=16, word='USE'),
 Row(index=17, word='receiving'),
 Row(index=18, word='Among'),
 Row(index=19, word='IMPLIED,'),
 Row(index=20, word='modification,'),
 Row(index=21, word='[3]'),
 Row(index=22, word='references'),
 Row(index=23, word='instance,'),
 Row(index=24, word='annual'),
 Row(index=25, word='return.'),
 Row(index=26, word='monthly'),
 Row(index=27, word='this,'),
 Row(index=28, word='induced'),
 Row(index=29, word='consequently'),
 Row(index=30, word='score'),
 Row(index=31, word='olde

In [13]:
# Use broadcast so workers can share the dictionary
dictionary = {}
for row in all_words:
    dictionary[row['word']] = row['index']
    
broadcastDictionary = spark.sparkContext.broadcast(dictionary)

def mapToDictionaryId(word):
    return broadcastDictionary.value[word]    


In [14]:
from  pyspark.sql.functions import input_file_name

In [15]:
df = spark.read.text("dataset/*")

In [16]:
df = df.withColumn("filename", input_file_name())

In [17]:
import os.path 
def get_file_index(filename):
    return int(os.path.basename(filename))

get_file_index('file:/Users/jiunjiunma/workspace/data-engineering-coding-challenge/dataset/0')

0

In [18]:
#df1 = df.rdd.map(lambda row: (row[0], get_file_index(row[1]))).toDF()
rdd1 = df.rdd.flatMap(lambda row: [ (mapToDictionaryId(s), get_file_index(row[1])) for s in row[0].split(" ")])


In [19]:
# row[0] is word id, row[1] is fild id
rdd2 = rdd1.map(lambda row: ((row[0], row[1]), row[1])).reduceByKey(lambda a,b:b).sortByKey()

In [20]:
rdd3 = rdd2.map(lambda row: row[0])

In [29]:
grouped = rdd3.groupByKey(1).collect()

In [34]:
for inverted_index in grouped:
    word_id = inverted_index[0]
    fileIdList = inverted_index[1]
    pair = (word_id, [fileId for fileId in fileIdList])
    print(pair)
    

(0, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44])
(1, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44])
(2, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44])
(3, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44])
(4, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44])
(5, [8, 12, 17, 32])
(6, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 

(1491, [18])
(1492, [18])
(1493, [18])
(1494, [18])
(1495, [18])
(1496, [18])
(1497, [18])
(1498, [18])
(1499, [18])
(1500, [18])
(1501, [18])
(1502, [18])
(1503, [18])
(1504, [18])
(1505, [18])
(1506, [18])
(1507, [18])
(1508, [18])
(1509, [18])
(1510, [18])
(1511, [18])
(1512, [18])
(1513, [18])
(1514, [18])
(1515, [18, 30, 36])
(1516, [18])
(1517, [27])
(1518, [27])
(1519, [3, 4, 6, 15, 21, 22, 24, 27])
(1520, [17, 27])
(1521, [6, 27])
(1522, [22, 24, 27])
(1523, [27])
(1524, [27])
(1525, [4, 9, 16, 27, 36, 40, 41])
(1526, [6, 12, 26, 27, 43])
(1527, [2, 27, 44])
(1528, [19, 27, 43])
(1529, [27])
(1530, [27])
(1531, [27])
(1532, [27])
(1533, [27])
(1534, [27])
(1535, [27])
(1536, [1, 3, 23, 27, 41])
(1537, [3, 27])
(1538, [27])
(1539, [21, 27])
(1540, [27])
(1541, [27])
(1542, [27])
(1543, [5, 8, 9, 23])
(1544, [0, 1, 3, 4, 7, 9, 11, 15, 17, 19, 23, 30, 43])
(1545, [3, 9, 19])
(1546, [9, 23])
(1547, [9])
(1548, [9])
(1549, [9, 44])
(1550, [3, 9, 11, 17, 44])
(1551, [9])
(1552, [0, 1

(2490, [0])
(2491, [0])
(2492, [0])
(2493, [0])
(2494, [0])
(2495, [0, 16, 17])
(2496, [0])
(2497, [0])
(2498, [0])
(2499, [0])
(2500, [0])
(2501, [0])
(2502, [0])
(2503, [0])
(2504, [0])
(2505, [0])
(2506, [0])
(2507, [0])
(2508, [0])
(2509, [0])
(2510, [0])
(2511, [0, 1])
(2512, [0])
(2513, [0])
(2514, [0])
(2515, [0])
(2516, [0])
(2517, [0])
(2518, [0])
(2519, [0])
(2520, [0])
(2521, [0])
(2522, [0])
(2523, [0])
(2524, [0])
(2525, [0])
(2526, [0])
(2527, [0])
(2528, [0, 14])
(2529, [0])
(2530, [0])
(2531, [0])
(2532, [0, 23])
(2533, [0])
(2534, [0])
(2535, [0])
(2536, [0, 37])
(2537, [0])
(2538, [0])
(2539, [0])
(2540, [0])
(2541, [0])
(2542, [0])
(2543, [0])
(2544, [0])
(2545, [0])
(2546, [0])
(2547, [0])
(2548, [0])
(2549, [0, 23])
(2550, [0, 26])
(2551, [0])
(2552, [0])
(2553, [0])
(2554, [0])
(2555, [0])
(2556, [0, 3, 12])
(2557, [0])
(2558, [0])
(2559, [0])
(2560, [0, 1])
(2561, [0, 2, 24])
(2562, [0])
(2563, [0])
(2564, [0])
(2565, [0])
(2566, [0])
(2567, [0])
(2568, [0])
(256

(3490, [2, 17])
(3491, [2, 17, 36])
(3492, [17])
(3493, [17])
(3494, [1, 17])
(3495, [3, 17])
(3496, [17])
(3497, [17])
(3498, [2, 17])
(3499, [17])
(3500, [17])
(3501, [17])
(3502, [17])
(3503, [2, 17, 31])
(3504, [17])
(3505, [17])
(3506, [2, 17])
(3507, [17])
(3508, [17])
(3509, [17])
(3510, [17])
(3511, [2, 4, 14, 17])
(3512, [17])
(3513, [17])
(3514, [2, 17])
(3515, [17])
(3516, [8, 17, 21])
(3517, [17])
(3518, [17])
(3519, [2, 17, 24, 41])
(3520, [17])
(3521, [17])
(3522, [17])
(3523, [17])
(3524, [17])
(3525, [17])
(3526, [17])
(3527, [17])
(3528, [2, 17])
(3529, [17])
(3530, [17])
(3531, [17, 19])
(3532, [2, 15, 17, 21, 23, 43])
(3533, [17])
(3534, [17, 21, 22])
(3535, [2, 8, 14, 17, 19, 24, 43, 44])
(3536, [17, 26, 41])
(3537, [17])
(3538, [17, 19])
(3539, [17])
(3540, [2, 15, 17])
(3541, [1, 3, 10, 17, 26])
(3542, [1])
(3543, [1])
(3544, [1])
(3545, [1, 8, 12, 19, 37])
(3546, [1])
(3547, [1])
(3548, [1])
(3549, [1, 3, 30, 38])
(3550, [1])
(3551, [1])
(3552, [1])
(3553, [1, 24

(4489, [15, 36])
(4490, [36])
(4491, [36])
(4492, [36])
(4493, [36])
(4494, [36])
(4495, [36])
(4496, [36])
(4497, [36, 39])
(4498, [4, 36])
(4499, [30, 36])
(4500, [36])
(4501, [36])
(4502, [36])
(4503, [36])
(4504, [36])
(4505, [36])
(4506, [36])
(4507, [36])
(4508, [36])
(4509, [36])
(4510, [36])
(4511, [36])
(4512, [36])
(4513, [36])
(4514, [36])
(4515, [36])
(4516, [36])
(4517, [36])
(4518, [14, 36])
(4519, [36])
(4520, [36])
(4521, [36])
(4522, [36])
(4523, [36])
(4524, [36])
(4525, [36])
(4526, [36])
(4527, [36])
(4528, [36])
(4529, [14, 36])
(4530, [36])
(4531, [36])
(4532, [36])
(4533, [36])
(4534, [36])
(4535, [36])
(4536, [36])
(4537, [36])
(4538, [2, 15, 36])
(4539, [36])
(4540, [2, 36])
(4541, [36])
(4542, [36])
(4543, [36])
(4544, [36])
(4545, [36])
(4546, [36])
(4547, [3, 15, 36, 41])
(4548, [36])
(4549, [36])
(4550, [36])
(4551, [36])
(4552, [36])
(4553, [36])
(4554, [36])
(4555, [36])
(4556, [36])
(4557, [36])
(4558, [36])
(4559, [36])
(4560, [36])
(4561, [36])
(4562, 

...

(288871, [18])
(288872, [18])
(288873, [18])
(288874, [18])
(288875, [18])
(288876, [18])
(288877, [18])
(288878, [18])
(288879, [18])
(288880, [18])
(288881, [12, 18, 27, 31])
(288882, [18])
(288883, [4, 9, 12, 18])
(288884, [18])
(288885, [18])
(288886, [18])
(288887, [18])
(288888, [18])
(288889, [18])
(288890, [18])
(288891, [18])
(288892, [18])
(288893, [18])
(288894, [18])
(288895, [18, 19])
(288896, [0, 1, 18, 21, 39])
(288897, [18])
(288898, [18])
(288899, [2, 18])
(288900, [18])
(288901, [18])
(288902, [18])
(288903, [18])
(288904, [18])
(288905, [18])
(288906, [18])
(288907, [18])
(288908, [18])
(288909, [18])
(288910, [18])
(288911, [1, 5, 18, 23, 42, 43])
(288912, [18])
(288913, [0, 18])
(288914, [18])
(288915, [18])
(288916, [18])
(288917, [18])
(288918, [18])
(288919, [18])
(288920, [18])
(288921, [18])
(288922, [18])
(288923, [18])
(288924, [18])
(288925, [2, 4, 15, 23, 27, 43])
(288926, [27])
(288927, [1, 11, 12, 15, 19, 23, 27])
(288928, [12, 19, 23, 27, 42])
(288929, 

(289871, [0])
(289872, [0])
(289873, [0])
(289874, [0])
(289875, [0])
(289876, [0])
(289877, [0])
(289878, [0])
(289879, [0])
(289880, [0])
(289881, [0])
(289882, [0, 3, 4, 12, 19, 39])
(289883, [0])
(289884, [0])
(289885, [0])
(289886, [0])
(289887, [0])
(289888, [0])
(289889, [0])
(289890, [0, 1])
(289891, [0])
(289892, [0])
(289893, [0])
(289894, [0])
(289895, [0])
(289896, [0])
(289897, [0])
(289898, [0])
(289899, [0, 3, 39])
(289900, [0])
(289901, [0])
(289902, [0])
(289903, [0])
(289904, [0, 1, 19, 40])
(289905, [0, 16])
(289906, [0])
(289907, [0])
(289908, [0])
(289909, [0])
(289910, [0, 12, 14])
(289911, [0])
(289912, [0])
(289913, [0])
(289914, [0, 3])
(289915, [0])
(289916, [0])
(289917, [0])
(289918, [0])
(289919, [0, 12])
(289920, [0])
(289921, [0])
(289922, [0, 41])
(289923, [0])
(289924, [0])
(289925, [0])
(289926, [0])
(289927, [0])
(289928, [0])
(289929, [0])
(289930, [0, 3])
(289931, [0])
(289932, [0])
(289933, [0])
(289934, [0])
(289935, [0])
(289936, [0])
(289937, [0

(291370, [19])
(291371, [19])
(291372, [19])
(291373, [19])
(291374, [2, 3, 19, 40, 43])
(291375, [19])
(291376, [19])
(291377, [3, 19])
(291378, [19])
(291379, [19])
(291380, [3, 19, 44])
(291381, [19])
(291382, [19])
(291383, [15, 19, 21, 26, 41])
(291384, [19, 21])
(291385, [19])
(291386, [19])
(291387, [19])
(291388, [13, 19])
(291389, [19])
(291390, [19])
(291391, [19])
(291392, [19])
(291393, [19])
(291394, [19])
(291395, [19])
(291396, [19])
(291397, [19])
(291398, [19, 26])
(291399, [19, 44])
(291400, [19])
(291401, [19, 40, 41])
(291402, [19])
(291403, [19])
(291404, [19])
(291405, [19])
(291406, [19])
(291407, [14, 15, 19, 23, 30, 38, 40])
(291408, [19])
(291409, [19])
(291410, [19])
(291411, [3, 12, 19, 31])
(291412, [19, 23])
(291413, [19])
(291414, [19])
(291415, [4, 15, 19])
(291416, [19])
(291417, [2, 3, 19, 43, 44])
(291418, [19])
(291419, [19])
(291420, [19])
(291421, [12, 26, 39])
(291422, [26])
(291423, [26])
(291424, [26])
(291425, [26])
(291426, [2, 26])
(291427, [

(292370, [41])
(292371, [41])
(292372, [41])
(292373, [41])
(292374, [41])
(292375, [41])
(292376, [41])
(292377, [41])
(292378, [41])
(292379, [41])
(292380, [41])
(292381, [41])
(292382, [41])
(292383, [41])
(292384, [41])
(292385, [41])
(292386, [41])
(292387, [41])
(292388, [41])
(292389, [41])
(292390, [41])
(292391, [41])
(292392, [41])
(292393, [41])
(292394, [24])
(292395, [24])
(292396, [24])
(292397, [24])
(292398, [24])
(292399, [2, 24])
(292400, [24])
(292401, [24])
(292402, [2, 24])
(292403, [24])
(292404, [24])
(292405, [24])
(292406, [24])
(292407, [24])
(292408, [24])
(292409, [3, 24])
(292410, [24])
(292411, [24])
(292412, [24])
(292413, [24])
(292414, [24])
(292415, [24])
(292416, [14, 24])
(292417, [24])
(292418, [24])
(292419, [24])
(292420, [24])
(292421, [24])
(292422, [24])
(292423, [24])
(292424, [24])
(292425, [24])
(292426, [4, 13, 14, 24])
(292427, [24])
(292428, [24])
(292429, [24])
(292430, [24])
(292431, [24])
(292432, [23])
(292433, [23])
(292434, [23])
(

(293369, [12])
(293370, [12])
(293371, [12])
(293372, [12])
(293373, [12])
(293374, [12])
(293375, [12])
(293376, [12])
(293377, [12])
(293378, [12])
(293379, [12])
(293380, [12])
(293381, [12])
(293382, [12])
(293383, [12])
(293384, [12])
(293385, [12])
(293386, [12])
(293387, [12])
(293388, [12])
(293389, [12])
(293390, [12])
(293391, [12])
(293392, [12])
(293393, [12])
(293394, [12])
(293395, [12])
(293396, [12])
(293397, [12])
(293398, [12])
(293399, [12])
(293400, [12])
(293401, [12])
(293402, [12])
(293403, [12])
(293404, [12])
(293405, [12])
(293406, [12])
(293407, [12])
(293408, [12])
(293409, [12])
(293410, [12])
(293411, [12])
(293412, [12])
(293413, [12])
(293414, [12])
(293415, [12])
(293416, [12])
(293417, [12])
(293418, [12])
(293419, [12])
(293420, [12])
(293421, [12])
(293422, [12])
(293423, [12])
(293424, [12])
(293425, [12])
(293426, [12])
(293427, [12])
(293428, [12])
(293429, [12])
(293430, [12])
(293431, [12])
(293432, [12])
(293433, [12])
(293434, [12])
(293435, [